In [211]:
import utilities as u
import find_r_peaks 
import preprocess_for_r_peaks
import emrich_vg.src.vg_beat_detectors as vg

from pathlib import Path

import polars as pl
import numpy as np
from plotly import express as px
from scipy.ndimage import median_filter
from scipy.signal import savgol_filter
from neurokit2 import signal_filter, signal_detrend
import pywt
from pywt import dwt
from scipy.interpolate import splrep, BSpline
import plotly.graph_objs as go

In [184]:
split_info_path = Path("../processed_data/split_info")
training_hf_path = Path(split_info_path, "fold_0/fold_0/training/training.parquet.snappy")
training_hf = pl.scan_parquet(training_hf_path)
ecg_paths = training_hf.select("ecg_path").collect().to_series()

In [6]:
ecg = u.read_matrix(ecg_paths[0])

In [7]:
sampling_freq = 500
fast_nvg = vg.FastNVG(
    sampling_frequency=sampling_freq
)

In [8]:
ecg[:, 1].shape

(5000,)

In [6]:
fast_nvg.find_peaks(
    sig=ecg[:, 1]
)

array([ 548, 1116, 1686, 2284, 2859, 3454, 4019, 4609])

In [9]:
wfdb_path = Path(
    "..",
    "raw_data", 
    "a-large-scale-12-lead-electrocardiogram-database-for-arrhythmia-study-1.0.0",
    "WFDBRecords"
)

ecg_paths = wfdb_path.glob(
        pattern="*/*/*.mat"
    )

How well does the detrending work?

In [158]:
patient_id = "JS01059"
preprocessed_path = "".join(["../processed_data/split_info/fold_0/fold_0/training/preprocessed_lead_II/", patient_id, ".mat"])
ecg_path = u.get_wanted_file_paths(wfdb_path, [patient_id])[0]
lead_II_test_before = u.get_leads("II", ecg=u.read_matrix(ecg_path)).ravel()

px.line(y=lead_II_test_before)

In [159]:
lead_II_test_after = u.read_matrix("".join(["../processed_data/split_info/fold_0/fold_0/training/preprocessed_lead_II/", patient_id, ".mat"])).ravel()
px.line(y=lead_II_test_after)

In [10]:
lead_II_test_after = u.read_matrix("".join(["../processed_data/split_info/fold_0/fold_0/training/preprocessed_lead_II_polynomial_version/", patient_id, ".mat"])).ravel()
px.line(y=lead_II_test_after)

In [11]:
lead_II_test_after = u.read_matrix("".join(["../processed_data/split_info/fold_0/fold_0/training/preprocessed_lead_II_polynomial_order_2/", patient_id, ".mat"])).ravel()
px.line(y=lead_II_test_after)

In [12]:
quantiles = np.quantile(
    a=lead_II_test_before,
    q=[0.40, 0.60]
)
lead_II_test_before_middle = lead_II_test_before[np.logical_and(lead_II_test_before >= quantiles[0], lead_II_test_before <= quantiles[1])]

In [14]:
px.line(y=lead_II_test_before_middle)

In [15]:
origin = np.linspace(
    start=-500,
    stop=500,
    num=500*10,
    dtype=np.int64
)

In [16]:
origin

array([-500, -500, -500, ...,  499,  499,  500])

In [33]:
a = np.arange(0, 5000, sampling_freq)
b = np.arange(sampling_freq, 5000 + sampling_freq, sampling_freq)

In [146]:
window_length = sampling_freq

observation_windows = u.get_intervals(
    start=0, 
    lengths=window_length + 1, 
    spacings=-1, 
    num_intervals=10
)
# np.quantile(
#     a=lead_II_test_before[2611:3051],
#     q=[0.10, 0.75]
# )
# lead_II_test_before_middle = lead_II_test_before[np.logical_and(lead_II_test_before >= quantiles[0], lead_II_test_before <= quantiles[1])]
quantiles = np.empty(shape=(len(observation_windows),), dtype=np.float64)
for i, w in enumerate(observation_windows):
    a, b = w
    # quantiles[i] = np.median(lead_II_test_before[a:b])
    cutoffs = np.quantile(
        a=lead_II_test_before[a:b],
        q=[0.10, 0.75]
    )
    lead_II_test_before_trimmed = lead_II_test_before[np.logical_and(lead_II_test_before >= cutoffs[0], lead_II_test_before <= cutoffs[1])]
    quantiles[i] = np.quantile(lead_II_test_before_trimmed, 0.58)

# Repeat the medians so that they are easier to work with.
repeated_medians = np.repeat(
    a=quantiles,
    repeats=window_length,
    axis=0
)

In [147]:
repeated_medians.shape

(5000,)

In [148]:
x=np.arange(len(repeated_medians))
y=repeated_medians
px.line(
    x=x,
    y=y
)

In [149]:
x=np.concatenate(
    (np.arange(-window_length, 0), np.arange(len(repeated_medians)), np.arange(5001, 5000 + window_length + 1))
)
y=np.concatenate(
    (repeated_medians[0:window_length], repeated_medians, repeated_medians[-window_length:])
)

In [150]:
px.line(
    x=x,
    y=y
)

In [151]:
fit = np.polynomial.polynomial.Polynomial.fit(
    x=x,
    y=y,
    deg=10,
    window=[-window_length, 5000 + window_length]
)

repeated_medians_smoothed = np.polynomial.polynomial.polyval(
    x=np.arange(len(repeated_medians)),
    c=fit.coef
)

In [121]:
fit

Polynomial([-1.54685837e+01, -3.94068868e-03,  4.79743113e-06,  1.23480030e-08,
       -1.33011814e-11, -5.50779331e-15,  9.23625550e-18, -3.77794536e-21,
        7.25024486e-25, -6.83116382e-29,  2.55703534e-33], domain=[-1000.,  6000.], window=[-1000.,  6000.], symbol='x')

In [152]:
px.line(y=repeated_medians_smoothed)

In [160]:
detrended_lead_II = lead_II_test_before-repeated_medians_smoothed
px.line(y=detrended_lead_II)

In [163]:
tarvainen2002_detrended_lead_II = signal_detrend(
    signal=lead_II_test_before.ravel(),
    method="tarvainen2002"  
)

In [164]:
px.line(y=tarvainen2002_detrended_lead_II)

In [95]:
x=np.arange(len(repeated_medians))
tck = splrep(x=x, y=repeated_medians, k=2, s=10)
my_spline = BSpline(*tck)

In [96]:
px.line(y=my_spline(x))

In [84]:
repeated_medians_smoothed = s(np.arange(len(repeated_medians)))

In [85]:
px.line(y=repeated_medians_smoothed)

In [49]:
repeated_medians_dispersion = 0.25 * (np.max(repeated_medians) - np.min(repeated_medians))
repeated_medians_with_noise = repeated_medians + np.random.normal(loc=0, scale=repeated_medians_dispersion, size=repeated_medians.shape[0])

In [51]:
px.line(y=repeated_medians_with_noise)

In [30]:
print(pywt.wavelist(kind='discrete'))

['bior1.1', 'bior1.3', 'bior1.5', 'bior2.2', 'bior2.4', 'bior2.6', 'bior2.8', 'bior3.1', 'bior3.3', 'bior3.5', 'bior3.7', 'bior3.9', 'bior4.4', 'bior5.5', 'bior6.8', 'coif1', 'coif2', 'coif3', 'coif4', 'coif5', 'coif6', 'coif7', 'coif8', 'coif9', 'coif10', 'coif11', 'coif12', 'coif13', 'coif14', 'coif15', 'coif16', 'coif17', 'db1', 'db2', 'db3', 'db4', 'db5', 'db6', 'db7', 'db8', 'db9', 'db10', 'db11', 'db12', 'db13', 'db14', 'db15', 'db16', 'db17', 'db18', 'db19', 'db20', 'db21', 'db22', 'db23', 'db24', 'db25', 'db26', 'db27', 'db28', 'db29', 'db30', 'db31', 'db32', 'db33', 'db34', 'db35', 'db36', 'db37', 'db38', 'dmey', 'haar', 'rbio1.1', 'rbio1.3', 'rbio1.5', 'rbio2.2', 'rbio2.4', 'rbio2.6', 'rbio2.8', 'rbio3.1', 'rbio3.3', 'rbio3.5', 'rbio3.7', 'rbio3.9', 'rbio4.4', 'rbio5.5', 'rbio6.8', 'sym2', 'sym3', 'sym4', 'sym5', 'sym6', 'sym7', 'sym8', 'sym9', 'sym10', 'sym11', 'sym12', 'sym13', 'sym14', 'sym15', 'sym16', 'sym17', 'sym18', 'sym19', 'sym20']


In [44]:
repeated_medians_smoothed, _ = dwt(
    data=repeated_medians,
    wavelet="sym20"
)

In [45]:
px.line(y=repeated_medians_smoothed)

In [154]:
lead_II_test_median_filter_savgol = savgol_filter(
    x=repeated_medians,
    window_length=sampling_freq,
    polyorder=2,
    mode="mirror"
)

In [155]:
px.line(y=lead_II_test_median_filter_savgol)

In [14]:
slice(*c[0])

slice(0, 501, None)

In [20]:
lead_II_test_median_filter = median_filter(
    input=lead_II_test_before,
    size=500,
    mode="constant",
    cval=np.median(lead_II_test_before),
    origin=0
)

In [18]:
px.line(y=lead_II_test_median_filter)

In [19]:
lead_II_tricky_1 = lead_II_test_before - lead_II_test_median_filter
px.line(y=lead_II_tricky_1)

In [27]:
lead_II_test_median_filter_savgol = savgol_filter(
    x=lead_II_test_median_filter,
    window_length=sampling_freq,
    polyorder=1,
    mode="mirror"
)

In [28]:
px.line(y=lead_II_test_median_filter_savgol)

In [33]:
lead_II_tricky = lead_II_test_before - lead_II_test_median_filter_savgol
px.line(y=lead_II_tricky)

In [156]:
power_line_freq = 50
lead_II_test_power_line = signal_filter(
    signal=lead_II_test_before,
    sampling_rate=sampling_freq,
    method="powerline",
    powerline=power_line_freq
)

In [157]:
px.line(y=lead_II_test_power_line)

Quantile for baseline?

In [130]:
np.quantile(lead_II_test_before[426:869], q=np.linspace(0, 1, 50))

array([-127.        , -102.        ,  -93.        ,  -88.        ,
        -83.        ,  -73.        ,  -63.        ,  -54.        ,
        -53.18367347,  -49.        ,  -44.        ,  -44.        ,
        -39.        ,  -39.        ,  -34.        ,  -34.        ,
        -29.        ,  -29.        ,  -24.        ,  -24.        ,
        -24.        ,  -20.        ,  -20.        ,  -15.        ,
        -15.        ,  -15.        ,  -10.        ,   -7.24489796,
         -5.        ,   -5.        ,    0.        ,    0.        ,
          0.        ,    5.        ,    5.        ,   10.        ,
         15.        ,   29.        ,   39.        ,   57.97959184,
         68.        ,   88.        ,   98.        ,  116.3877551 ,
        145.59183673,  171.        ,  189.69387755,  205.        ,
        341.48979592,  566.        ])

In [136]:
quantiles = np.quantile(
    a=lead_II_test_before[2611:3051],
    q=[0.10, 0.75]
)
lead_II_test_before_middle = lead_II_test_before[np.logical_and(lead_II_test_before >= quantiles[0], lead_II_test_before <= quantiles[1])]

np.quantile(lead_II_test_before_middle[2611:3051], q=0.58)

-11.90000000000012

In [134]:
50/85

0.5882352941176471

What happens if we try to find a file path that doesn't exist?

In [176]:
g = u.get_wanted_file_paths(
    parent_dir=Path("../processed_data/split_info/fold_0/fold_0/training"),
    file_stems=["JS01053", "TS3"]
    # file_stems=["JS01053"]
)

In [177]:
g

[PosixPath('../processed_data/split_info/fold_0/fold_0/training/preprocessed_lead_II/JS01053.mat')]

How are our R peaks looking?

In [242]:
r_peak_info = pl.scan_parquet(
    source=Path("../processed_data/extracted_features/r_peak_info.parquet.snappy")
)

In [244]:
r_peak_info.fetch()

shape: (500, 2)
┌────────────┬────────────────────┐
│ patient_id ┆ r_peak             │
│ ---        ┆ ---                │
│ str        ┆ list[i64]          │
╞════════════╪════════════════════╡
│ JS01053    ┆ [129, 619, … 4556] │
│ JS01054    ┆ [210, 487, … 4968] │
│ JS01055    ┆ [81, 318, … 4766]  │
│ JS01056    ┆ [177, 416, … 4856] │
│ JS01057    ┆ [245, 900, … 4883] │
│ …          ┆ …                  │
│ JS01562    ┆ [95, 347, … 4898]  │
│ JS01563    ┆ [217, 513, … 4993] │
│ JS01564    ┆ [106, 400, … 4818] │
│ JS01565    ┆ [7, 436, … 4555]   │
│ JS01566    ┆ [106, 381, … 4789] │
└────────────┴────────────────────┘

In [238]:
patient_id = "JS01054"
r_peaks = (r_peak_info
    .filter(pl.col("patient_id") == patient_id)
    .select(pl.col("r_peaks").explode()).collect()
    .to_series()
)
len(r_peaks)

18

In [206]:
preprocessed_path = "".join(["../processed_data/split_info/fold_0/fold_0/training/preprocessed_lead_II/", patient_id, ".mat"])
ecg_path = u.get_wanted_file_paths(wfdb_path, [patient_id])[0]
lead_II = u.get_leads("II", ecg=u.read_matrix(ecg_path)).ravel()

In [207]:
px.line(
    y=lead_II
)

In [208]:
preprocessed_path = "".join(["../processed_data/split_info/fold_0/fold_0/training/preprocessed_lead_II/", patient_id, ".mat"])
lead_II = u.read_matrix(preprocessed_path).ravel()

In [222]:
# https://stackoverflow.com/a/69893714/8423001
fig1 = px.line(
    x=np.linspace(0, 10, num=sampling_freq*10),
    y=lead_II
)

In [229]:
# https://stackoverflow.com/a/63414176/8423001
fig2 = px.scatter(
    x=[r_peak_obs_index/sampling_freq for r_peak_obs_index in r_peaks],
    y=lead_II[r_peaks]
)
fig2.update_traces(marker=dict(color='red'))
fig3 = go.Figure(data=fig1.data + fig2.data)

fig3.show()

Given the R peaks, what are the indices for slicing the signal?

In [237]:
for i in range(len(r_peaks) - 1):
    print(ecg[slice(r_peaks[i], r_peaks[i + 1] + 1), :].shape)

(278, 12)
(277, 12)
(281, 12)
(281, 12)
(280, 12)
(281, 12)
(281, 12)
(280, 12)
(283, 12)
(280, 12)
(281, 12)
(283, 12)
(279, 12)
(283, 12)
(283, 12)
(282, 12)
(282, 12)
